<a href="https://colab.research.google.com/github/avkumar/RAD-NeRF/blob/main/Copy_of_RAD_NeRF_demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# [RAD-NeRF](https://github.com/ashawkey/RAD-NeRF) for Real-time Neural Talking Portrait Synthesis

### Check the machine

In [126]:
! nvidia-smi

Sat Mar 25 05:05:16 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.85.12    Driver Version: 525.85.12    CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   64C    P0    27W /  70W |   1737MiB / 15360MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [127]:
#@title install dependencies
! git clone https://github.com/ashawkey/RAD-NeRF.git

%cd RAD-NeRF

%mkdir -p pretrained
%mkdir -p data

Cloning into 'RAD-NeRF'...
remote: Enumerating objects: 124, done.
remote: Counting objects: 100% (31/31), done.
remote: Compressing objects: 100% (16/16), done.
remote: Total 124 (delta 20), reused 15 (delta 15), pack-reused 93
Receiving objects: 100% (124/124), 115.58 KiB | 14.45 MiB/s, done.
Resolving deltas: 100% (36/36), done.
/content/RAD-NeRF/RAD-NeRF


In [128]:
# install (slow...)
! apt install libasound2-dev portaudio19-dev libportaudio2 libportaudiocpp0 ffmpeg
! pip install -r requirements.txt
! pip install ffmpeg-python
! bash scripts/install_ext.sh

Reading package lists... Done
Building dependency tree       
Reading state information... Done
libportaudio2 is already the newest version (19.6.0-1build1).
libportaudiocpp0 is already the newest version (19.6.0-1build1).
portaudio19-dev is already the newest version (19.6.0-1build1).
libasound2-dev is already the newest version (1.2.2-2.1ubuntu2.5).
ffmpeg is already the newest version (7:4.2.7-0ubuntu0.1).
0 upgraded, 0 newly installed, 0 to remove and 23 not upgraded.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Processing ./freqencoder
  Preparing metadata (setup.py) ... done
  Created wheel for freqencoder: filename=freqencoder-0.0.0-cp39-cp39-linux_x86_64.whl size=2556639 sha256=a182e10ab70e9d1c641339a88e56da5b381875a31da2d5e11636f

# Settings
* Person: choose a pretrained person-specific model.
* Audio: choose a provided audio file, or upload your own (choose `custom`).
* Background: choose a provided background image, or upload your own (choose `custom`).
* Pose_start/end: data range to use from pose.json.

In [4]:
#@markdown ####**Settings:**
Person = 'engm' #@param ['obama', 'marco', 'engm', 'chris']
Audio = 'intro' #@param ['intro', 'nvp', 'custom']
Background = 'default' #@param ['default', 'custom']
Pose_start = 0 #@param {type: 'integer'}
Pose_end = 100 #@param {type: 'integer'}

In [5]:
#@title Upload audio if choose custom (*.wav format)
if Audio == 'custom':
    %cd data/
    from google.colab import files
    uploaded = files.upload()
    Aud = os.path.basename(next(iter(uploaded))) # filename, should be '*.wav'
    assert Aud[-4:] == '.wav', f'[ERROR] must upload *.wav audio file'
    %cd ..
else:
    Aud = Audio + '.wav'

print(f'[INFO] use audio file: {Aud}')

[INFO] use audio file: intro.wav


In [6]:
#@title Upload background image if choose custom
if Background == 'custom':
    %cd data/
    from google.colab import files
    uploaded = files.upload()
    BG = os.path.basename(next(iter(uploaded))) # filename, should be '*.wav'
    %cd ..
else:
    BG = 'bg.jpg'

print(f'[INFO] use background file: {BG}')

[INFO] use background file: bg.jpg


In [7]:
#@title Download things

import gdown

# model checkpoint and pose sequence
if Person == 'obama':
    gdown.download("https://drive.google.com/uc?id=1dlajKAkibAWRzNWaUdoFO0OKhVeeBW9w", "pretrained/model.pth", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1_PK1AZCpB7CCBiQsvOm14qr31K20TV9J", "data/pose.json", quiet=False)
elif Person == 'engm':
    gdown.download("https://drive.google.com/uc?id=1P4Fbg5IN_eWxkr7sVQJeK95WVnzV0yGs", "pretrained/model.pth", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1bmkohn1bnxkCJs9Igv5xXIBhyWKoyXMb", "data/pose.json", quiet=False)
elif Person == 'marco':
    gdown.download("https://drive.google.com/uc?id=1XkLbWF3CbvIaLTkjUd7zkdp03um1cyPL", "pretrained/model.pth", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1ETV7yyK3u4MC1ubUQbIvTrRAfJvypcUg", "data/pose.json", quiet=False)
elif Person == 'chris':
    gdown.download("https://drive.google.com/uc?id=1Mx2f1Iu-W9yG8QOn_2ROhhIcrVz4yMeA", "pretrained/model.pth", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1O8uvNuqMo4p0aJi16OMJXLsd1UeQ_7Dw", "data/pose.json", quiet=False)


# audio example
if Audio == 'intro':
    gdown.download("https://drive.google.com/uc?id=1gxfLuYuGFMlYz7BDxJlcfnDISN4sfbKg", "data/intro.wav", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1r2-wJ0VFfahE4bdDzGgvoC2tU24XmxPu", "data/intro_eo.npy", quiet=False)
elif Audio == 'nvp':
    gdown.download("https://drive.google.com/uc?id=1WgtSiB_gLZZ-b8IO_KIVwT_ZRPUSx7yY", "data/nvp.wav", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1UKCW67Idw00_3QqzXasN_dvYXlYC37fe", "data/nvp_eo.npy", quiet=False)


# background image
if Background == 'default':
    gdown.download("https://drive.google.com/uc?id=1RDiRCFXMk3hQ0hzKVculQdFqisayT1MM", "data/bg.jpg", quiet=False)

Downloading...
From: https://drive.google.com/uc?id=1P4Fbg5IN_eWxkr7sVQJeK95WVnzV0yGs
To: /content/RAD-NeRF/pretrained/model.pth
100%|██████████| 17.3M/17.3M [00:00<00:00, 108MB/s] 
Downloading...
From: https://drive.google.com/uc?id=1bmkohn1bnxkCJs9Igv5xXIBhyWKoyXMb
To: /content/RAD-NeRF/data/pose.json
100%|██████████| 2.08M/2.08M [00:00<00:00, 179MB/s]
Downloading...
From: https://drive.google.com/uc?id=1gxfLuYuGFMlYz7BDxJlcfnDISN4sfbKg
To: /content/RAD-NeRF/data/intro.wav
100%|██████████| 752k/752k [00:00<00:00, 127MB/s]
Downloading...
From: https://drive.google.com/uc?id=1r2-wJ0VFfahE4bdDzGgvoC2tU24XmxPu
To: /content/RAD-NeRF/data/intro_eo.npy
100%|██████████| 1.66M/1.66M [00:00<00:00, 157MB/s]
Downloading...
From: https://drive.google.com/uc?id=1RDiRCFXMk3hQ0hzKVculQdFqisayT1MM
To: /content/RAD-NeRF/data/bg.jpg
100%|██████████| 51.3k/51.3k [00:00<00:00, 19.3MB/s]


In [8]:
#@title Extract audio features
if Audio == 'custom':
    # need to wait to download the ASR model
    %run nerf/asr.py --wav data/{Aud} --save_feats

In [9]:
#@title Run Inference
%run test.py -O --torso \
    --pose data/pose.json \
    --data_range {Pose_start} {Pose_end} \
    --ckpt pretrained/model.pth \
    --aud data/{Aud[:-4]}_eo.npy \
    --bg_img data/{BG} \
    --workspace trial

Namespace(pose='data/pose.json', aud='data/intro_eo.npy', bg_img='data/bg.jpg', O=True, data_range=[0, 100], workspace='trial', seed=0, ckpt='pretrained/model.pth', num_rays=65536, cuda_ray=True, max_steps=16, num_steps=16, upsample_steps=0, update_extra_interval=16, max_ray_batch=4096, fp16=True, lambda_amb=0.1, fbg=False, exp_eye=True, fix_eye=-1, smooth_eye=True, torso_shrink=0.8, color_space='srgb', bound=1, scale=4, offset=[0, 0, 0], dt_gamma=0.00390625, min_near=0.05, density_thresh=10, density_thresh_torso=0.01, patch_size=1, finetune_lips=False, smooth_lips=True, torso=True, head_ckpt='', gui=False, W=450, H=450, radius=3.35, fovy=21.24, max_spp=1, att=2, emb=False, ind_dim=4, ind_num=10000, ind_dim_torso=8, amb_dim=2, part=False, part2=False, train_camera=False, smooth_path=True, smooth_path_window=7, asr=False, asr_wav='', asr_play=False, asr_model='cpierse/wav2vec2-large-xlsr-53-esperanto', asr_save_feats=False, fps=50, l=10, m=50, r=10, test=True, test_train=False)


[INFO] Trainer: ngp | 2023-03-25_03-32-31 | cuda | fp16 | trial

[INFO] #parameters: 4231701

[INFO] Loading pretrained/model.pth ...

[INFO] loaded model.

...

[INFO] eye_area: 0.25 - 0.25


==> Start Test, save results to trial/results

100% 587/588 [00:56<00:00, 11.85it/s]

==> Finished Test.

100% 588/588 [01:07<00:00,  8.66it/s]


In [10]:
#@title Display Video

import os
import glob
from IPython.display import HTML
from base64 import b64encode

def get_latest_file(path):
  dir_list = glob.glob(path)
  dir_list.sort(key=lambda x: os.path.getmtime(x))
  return dir_list[-1]
 
Video = get_latest_file(os.path.join('trial', 'results', '*.mp4'))
Video_aud = Video.replace('.mp4', '_aud.mp4')

# concat audio
! ffmpeg -y -i {Video} -i data/{Aud} -c:v copy -c:a aac {Video_aud}

# display
def show_video(video_path, video_width=450):
   
  video_file = open(video_path, "r+b").read()
  video_url = f"data:video/mp4;base64,{b64encode(video_file).decode()}"

  return HTML(f"""<video width={video_width} controls><source src="{video_url}"></video>""")
  
show_video(Video_aud)

ffmpeg version 4.2.7-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 9 (Ubuntu 9.4.0-1ubuntu1~20.04.1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-avresample --disable-filter=resample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librsvg --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --e

### Cast to streamlit

In [ ]:
!pip install -q streamlit

In [ ]:
!pip install pyngrok

In [14]:
!ngrok authtoken 2NUPLuzLqNno0MBbFzeLzqAcuf8_3cLeUq7MFZyAGEVczyDc9

Authtoken saved to configuration file: /root/.ngrok2/ngrok.yml


In [15]:
from pyngrok import ngrok
public_url = ngrok.connect(port='8501')
public_url

<NgrokTunnel: "http://5b64-35-186-167-53.ngrok.io" -> "http://localhost:80">

In [133]:
path = "/content/RAD-NeRF/" + Video_aud

In [134]:
from IPython.core.magic import register_line_cell_magic

@register_line_cell_magic
def writetemplate(line, cell):
    with open(line, 'w') as f:
        f.write(cell.format(**globals()))

In [1]:
%%writetemplate streamlit_app.py

import streamlit as st
st.set_page_config(page_title="AI Therapy", page_icon=":robot:")
st.header("Video")
video_read = open("{path}", "rb") 
st.video(video_read)

UsageError: Cell magic `%%writetemplate` not found.


In [2]:
!streamlit run /content/RAD-NeRF/streamlit_app.py & npx localtunnel --port 8501

[#######...........] / extract:localtunnel: verb lock using /root/.npm/_locks/s


  You can now view your Streamlit app in your browser.

  Network URL: http://172.28.0.12:8501
  External URL: http://35.186.167.53:8501

npx: installed 22 in 5.199s
your url is: https://tough-brooms-walk-35-186-167-53.loca.lt
  Stopping...
^C
